In [4]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import datetime as dt
import os
from sklearn.metrics import mean_squared_error
from scipy.ndimage.interpolation import shift
from math import sin, cos, sqrt, atan2, radians 

import dateutil

from pathlib import Path

In [5]:
status_path = Path('../filtered_status.csv')
stations_path = Path('../station.csv')

In [6]:
status_df = pd.read_csv(status_path, parse_dates=['time'])
stations_df = pd.read_csv(stations_path)

In [7]:
status_df

station_id  bikes_available  docks_available                time
0                  2                2               25 2013-08-29 12:06:01
1                  2                2               25 2013-08-29 12:07:01
2                  2                2               25 2013-08-29 12:08:01
3                  2                2               25 2013-08-29 12:09:01
4                  2                2               25 2013-08-29 12:10:01
...              ...              ...              ...                 ...
71977905          84                8                7 2015-08-31 23:55:02
71977906          84                8                7 2015-08-31 23:56:01
71977907          84                8                7 2015-08-31 23:57:02
71977908          84                8                7 2015-08-31 23:58:02
71977909          84                8                7 2015-08-31 23:59:02

[71977910 rows x 4 columns]

In [8]:
stations_df

id                               name        lat        long  dock_count  \
0    2  San Jose Diridon Caltrain Station  37.329732 -121.901782          27   
1    3              San Jose Civic Center  37.330698 -121.888979          15   
2    4             Santa Clara at Almaden  37.333988 -121.894902          11   
3    5                   Adobe on Almaden  37.331415 -121.893200          19   
4    6                   San Pedro Square  37.336721 -121.894074          15   
..  ..                                ...        ...         ...         ...   
65  77                  Market at Sansome  37.789625 -122.400811          27   
66  80    Santa Clara County Civic Center  37.352601 -121.905733          15   
67  82          Broadway St at Battery St  37.798541 -122.400862          15   
68  83                         Mezes Park  37.491269 -122.236234          15   
69  84                        Ryland Park  37.342725 -121.895617          15   

             city installation_date  
0        San Jose          8/6/2013  
1        San Jose          8/5/2013  
2        San Jose          8/6/2013  
3        San Jose          8/5/2013  
4        San Jose          8/7/2013  
..            ...               ...  
65  San Francisco         8/25/2013  
66       San Jose        12/31/2013  
67  San Francisco         1/22/2014  
68   Redwood City         2/20/2014  
69       San Jose          4/9/2014  

[70 rows x 7 columns]

## Ottengo gli id delle stazioni per ogni città diversa

In [9]:
cities = stations_df['city'].unique()
cities

array(['San Jose', 'Redwood City', 'Mountain View', 'Palo Alto',
       'San Francisco'], dtype=object)

In [10]:
city_stations = {}

for city in cities:
    city_stations[city] = stations_df[stations_df['city'] == city]['id'].unique()

city_stations

{'San Jose': array([ 2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 16, 80, 84]),
 'Redwood City': array([21, 22, 23, 24, 25, 26, 83]),
 'Mountain View': array([27, 28, 29, 30, 31, 32, 33]),
 'Palo Alto': array([34, 35, 36, 37, 38]),
 'San Francisco': array([41, 42, 45, 46, 47, 48, 49, 50, 51, 39, 54, 55, 56, 57, 58, 59, 60,
        61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77,
        82])}

In [11]:
stations_id = city_stations['San Jose']
for id_station in stations_id:
    min_time = status_df[status_df['station_id']==id_station]['time'].min()
    max_time = status_df[status_df['station_id']==id_station]['time'].max()
    print(f"STATION {id_station}: min {min_time}, max {max_time}\n")


STATION 2: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 3: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 4: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 5: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 6: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 7: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 8: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 9: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 10: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 11: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 12: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 13: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 14: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 16: min 2013-08-29 12:06:01, max 2015-08-31 23:59:02

STATION 80: min 2013-12-31 10:29:03, max 2015-08-31 23:59:02

STATION 84: min 2014-04-09 12:40:02, max 2015-08-31 23:59:02



## Divido il dataset iniziale in fasce orarie

In [12]:
slots = {}
slots["0-6"] = status_df.set_index('time').between_time("0:00", "6:00", include_end=False).reset_index()
slots["6-10"] = status_df.set_index('time').between_time("6:00", "10:00", include_end=False).reset_index()
slots["10-14"] = status_df.set_index('time').between_time("10:00", "14:00", include_end=False).reset_index()
slots["14-17"] = status_df.set_index('time').between_time("14:00", "17:00", include_end=False).reset_index()
slots["17-20"] = status_df.set_index('time').between_time("17:00", "20:00", include_end=False).reset_index()
slots["20-24"] = status_df.set_index('time').between_time("20:00", "23:59:59", include_end=True).reset_index()

In [ ]:
interval=30
window_width = 5
cities_status_dfs = {}
cities_correaltion_dfs = {}

for city in cities:
    stations_id = city_stations[city]
    for slot in slots:
        current_df = slots[slot]
        merged_df = pd.DataFrame()
        for id_station in stations_id:
            new_df = pd.DataFrame()
            single_station_df = current_df[current_df['station_id']==id_station][['time', 'bikes_available']]
            windowing_df =  single_station_df.resample(f"{interval}T", on = 'time').mean()
            #resetto l'indice
            windowing_df  = windowing_df.reset_index()
            new_df['time'] = windowing_df['time']
            for i in reversed(range(window_width)):
                new_df[f'{id_station}_T{i}'] =  windowing_df['bikes_available'].shift(periods=i)
            if len(merged_df) == 0:
                merged_df = new_df.copy(deep=True)
                continue
            merged_df = pd.merge(merged_df, new_df, how='outer', on='time')

        city_str= city.replace(" ", "")
        cities_status_dfs[f"{city_str}_{slot}"]= merged_df
        if (Path.cwd() / f'Time_slots_results/{city_str}/{interval}_{window_width}').exists() == False:
            os.makedirs(f"./Time_slots_results/{city_str}/{interval}_{window_width}")
        merged_df.to_csv(f"./Time_slots_results/{city_str}/{interval}_{window_width}/{slot}_{city_str}_status.csv", index=False)

        city_correaltion = merged_df.corr()
        cities_correaltion_dfs[f"{city_str}_{slot}"]= city_correaltion
        city_correaltion.to_csv(f"./Time_slots_results/{city_str}/{interval}_{window_width}/Correlation_{slot}_{city_str}_status.csv")

        f = plt.figure(figsize=(19, 15))
        plt.matshow(merged_df.corr(), fignum=f.number)
        plt.xticks(range(merged_df.select_dtypes(['number']).shape[1]), merged_df.select_dtypes(['number']).columns, fontsize=14, rotation=90)
        plt.yticks(range(merged_df.select_dtypes(['number']).shape[1]), merged_df.select_dtypes(['number']).columns, fontsize=14)
        cb = plt.colorbar()
        cb.ax.tick_params(labelsize=14)
        plt.title(f'Correlation Matrix {city_str}, time slot {slot}, {interval} min, width {window_width}', fontsize=16);
        plt.savefig(f'./Time_slots_results/{city_str}/{interval}_{window_width}/CorrelationMatrix_{slot}_{city_str}_{interval}_{window_width}')

# single_station_df

windowing_df

In [16]:
# merged_df.head()

In [23]:

# cities_status_dfs["SanFrancisco_6-10"].corr().style.background_gradient(cmap='viridis')


In [30]:
# mask = cities_correaltion_dfs['RedwoodCity_6-10'].abs()<0.5
# new_df = cities_correaltion_dfs['RedwoodCity_6-10'].copy()
# new_df[mask] = -1 
# new_df.style.background_gradient(cmap='viridis')

## Calcolo la distanza tra le diverse stazioni

In [19]:
#function to retrieve distance between 2 stations
def getDistance(lat_a, long_a, lat_b, long_b):
    # approximate radius of earth in km
    R = 6373.0    
    lat1=radians(lat_a)
    lat2=radians(lat_b)
    lon1=radians(long_a)
    lon2=radians(long_b)
    
    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))

    distance = R * c
    return distance

In [20]:
coordinates_stations_df = stations_df[["id", "lat", "long"]]
records = coordinates_stations_df.to_records(index=False)
list_coo = list(records)
# print(list_coo)

voc_distances={}
for i in range(len(list_coo)):
    for j in range(i+1,len(list_coo)):
        station1=list_coo[i][0]
        station2=list_coo[j][0]
        lat_i=float(list_coo[i][1])
        long_i=float(list_coo[i][2])
        lat_j=float(list_coo[j][1])
        long_j=float(list_coo[j][2])
        distance=getDistance(lat_i, long_i, lat_j, long_j)
        id_stations=str(station1)+' '+str(station2)
        voc_distances[id_stations]=distance

In [21]:
voc_distances['69 70']

0.018559073076332665